In [1]:
!pip install groq

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.9/124.9 kB 3.1 MB/s eta 0:00:0000:01


In [70]:
import pandas as pd

file_path = "csv files/filtered_disagreement_identity_cases.csv"
chunk_size = 100000  

# Define threshold for long texts (e.g., min 300 characters)
MIN_CHAR_LENGTH = 300

long_texts = []
for chunk in pd.read_csv(file_path, chunksize=chunk_size):
    long_comments = chunk[chunk["comment_text_x"].str.len() > MIN_CHAR_LENGTH]
    long_texts.append(long_comments)

long_text_df = pd.concat(long_texts, ignore_index=True)

json_file_path = "long_disagreement_cases.json"
long_text_df.to_json(json_file_path, orient="records", lines=True)

print(f"Filtered {len(long_text_df)} long disagreement identity cases and saved to {json_file_path}.")


Filtered 19214 long disagreement identity cases and saved to long_disagreement_cases.json.


In [75]:
df = pd.read_csv(file_path)

    # Define long comment threshold (e.g., at least 100 words)
df["word_count"] = df["comment_text_x"].apply(lambda x: len(str(x).split()))
long_text_df = df[df["word_count"] > 100]

In [77]:
long_text_df[0:500].to_csv('kaggledata.csv')

In [18]:
import os
import random
import json
import pandas as pd
from typing import List, Dict
from groq import Groq  

with open('api_key.txt', 'r') as file:
    api_key = file.read().strip()

client = Groq(api_key=api_key)


class LLMManager:
    """Manages interactions with Groq API-based LLMs."""

    def __init__(self, model_name: str):
        self.model_name = model_name

    def generate_response(self, prompt: str) -> str:
        """Generates response using Groq API."""
        try:
            chat_completion = client.chat.completions.create(
                messages=[{"role": "user", "content": prompt}],
                model=self.model_name,  # Example: "mixtral-8x7b-32768"
            )
            response = chat_completion.choices[0].message.content
            return response.strip()
        except Exception as e:
            print(f"Error generating response: {e}")
            return "Error generating response."

class DiscussionSimulator:
    """Simulates discussions among multiple LLMs."""

    def __init__(self, llms: List[LLMManager]):
        self.llms = llms

    def simulate_discussion(self, task_description: str, max_rounds: int = 5) -> Dict:
        """Simulates a structured discussion among LLMs."""
        transcript = []
        context = task_description

        for round_num in range(max_rounds):
            round_transcript = {"round": round_num + 1, "responses": []}
            print(f"\n--- Round {round_num + 1} ---")

            for llm_idx, llm in enumerate(self.llms):
                prompt = f"Current discussion context: {context}\nWhat is your input for this round?"
                response = llm.generate_response(prompt)
                
                # Summarize the discussion in one sentence
                summary = llm.generate_response(f"Summarize in one sentence: {response}")

                context += f"\nLLM-{llm_idx + 1}: {summary}"
                round_transcript["responses"].append({"LLM": f"LLM-{llm_idx + 1}", "response": response, "summary": summary})

            transcript.append(round_transcript)

        return {"transcript": transcript, "final_output": context}

def thematic_coding(llms: List[LLMManager], comment: str) -> Dict[str, str]:
    """Assigns each LLM to generate a qualitative code for the full comment."""
    codes = {}
    for idx, llm in enumerate(llms):
        response = llm.generate_response(f"A code is often a word or short phrase that symbolically assigns a summative, salient, essence-capturing and/or evocative attribute to a portion of language-based or visual data. Perform thematic analysis on the following comment and generate a concise qualitative code:\n\n{comment}")
        codes[f"LLM-{idx + 1}"] = response
    return codes

def simulate_coding_discussion(llms: List[LLMManager], initial_codes: Dict[str, str]) -> Dict:
    """Simulates a discussion where LLMs refine qualitative codes together."""
    context = "Here are the initial codes proposed by each LLM:\n"
    memory = {}

    for llm, code in initial_codes.items():
        context += f"{llm}: {code}\n"
        memory[llm] = {"initial_code": code, "discussions": []}

    context += "\nCompare and refine the codes collaboratively."

    discussion_transcript = []
    for round_num in range(3):
        round_responses = []
        print(f"\n--- Round {round_num + 1} ---")

        for idx, llm in enumerate(llms):
            llm_id = f"LLM-{idx + 1}"
            prompt = f"Context: {context}\n\nWhat refinements do you suggest?"
            response = llm.generate_response(prompt)

            summary = llm.generate_response(f"Summarize in one sentence: {response}")
            memory[llm_id]["discussions"].append(summary)

            context += f"\n{llm_id}: {summary}"
            round_responses.append({"LLM": llm_id, "response": response, "summary": summary})

        discussion_transcript.append({"round": round_num + 1, "responses": round_responses})

    final_responses = []
    for idx, llm in enumerate(llms):
        final_context = "Final discussion summary:\n" + "\n".join(
            [summary for mem in memory.values() for summary in mem["discussions"]]
        )
        response = llm.generate_response(f"{final_context}\n\nGenerate the final agreed qualitative code.")
        final_responses.append({"LLM": f"LLM-{idx + 1}", "response": response})

    return {
        "initial_codes": initial_codes,
        "discussion_transcript": discussion_transcript,
        "final_codes": [res["response"] for res in final_responses],
        "memory": memory,
    }

def run_thematic_analysis(simulator, long_text_df: pd.DataFrame):
    """Runs the thematic analysis workflow on sampled long comments."""
    sampled_comments = long_text_df[0:500]["comment_text_x"].tolist()

    results = []
    for i, comment in enumerate(sampled_comments):
        print(f"\nProcessing comment {i+1}/{100}...\n")

        print("\nStep 1: Initial Thematic Coding")
        codes = thematic_coding(simulator.llms, comment)

        print("\nStep 2: LLMs Discuss and Refine Codes")
        discussion_results = simulate_coding_discussion(simulator.llms, codes)

        print("\nFinal Agreed Code:")
        print(discussion_results["final_codes"])

        results.append({
            "comment": comment,
            "initial_codes": codes,
            "discussion_results": discussion_results,
        })

    with open("results_3r_mixtral_llama70b_qwen_deepseek_gemma_1.json", "w") as f:
        json.dump(results, f, indent=2)

def main():
    """Main function to run the experiment on long comments."""
    llms = [
        LLMManager(model_name="mixtral-8x7b-32768"),
        LLMManager(model_name="llama-3.3-70b-versatile"),
        LLMManager(model_name="deepseek-r1-distill-qwen-32b"),
        LLMManager(model_name="qwen-2.5-32b"),
        LLMManager(model_name="gemma2-9b-it")
    ]

    simulator = DiscussionSimulator(llms)

    # Load and filter long comments
    file_path = "csv files/filtered_disagreement_identity_cases.csv"  # Ensure this file is prepared
    df = pd.read_csv(file_path)

    # Define long comment threshold (e.g., at least 100 words)
    df["word_count"] = df["comment_text_x"].apply(lambda x: len(str(x).split()))
    long_text_df = df[df["word_count"] > 100]

    if long_text_df.empty:
        print("No long comments found in dataset.")
        return

    run_thematic_analysis(simulator, long_text_df)

if __name__ == "__main__":
    main()



Processing comment 1/100...


Step 1: Initial Thematic Coding

Step 2: LLMs Discuss and Refine Codes

--- Round 1 ---

--- Round 2 ---

--- Round 3 ---

Final Agreed Code:
["Collaborative refinement of proposed codes is essential to effectively address the critique of inaction's harmful consequences and the unintended consequences of compassion, highlighting the need for policy change to tackle the urban humanitarian crisis affecting vulnerable populations.", 'The final agreed qualitative code is: "Inaction Enabling Harm & Compassion\'s Downside: A Call for Policy Change."', '<think>\nOkay, I need to generate a final qualitative code based on the discussion. The key themes are inaction leading to harm, the tension between compassion and enabling negative outcomes, the public health crisis related to drug addiction and mental illness, policy failures, the urgency for change, and unintended consequences of compassion.\n\nI should combine these themes into a concise code that captures al

In [66]:
import os
import random
import json
import pandas as pd
from typing import List, Dict
from groq import Groq  

with open('api_key.txt', 'r') as file:
    api_key = file.read().strip()

client = Groq(api_key=api_key)

class LLMManager:
    """Manages interactions with Groq API-based LLMs."""

    def __init__(self, model_name: str):
        self.model_name = model_name

    def generate_response(self, prompt: str) -> str:
        """Generates response using Groq API."""
        try:
            chat_completion = client.chat.completions.create(
                messages=[{"role": "user", "content": prompt}],
                model=self.model_name,  # Example: "mixtral-8x7b-32768"
            )
            response = chat_completion.choices[0].message.content
            return response.strip()
        except Exception as e:
            print(f"Error generating response: {e}")
            return "Error generating response."

class DiscussionSimulator:
    """Simulates discussions among multiple LLMs."""

    def __init__(self, llms: List[LLMManager]):
        self.llms = llms

    def simulate_discussion(self, task_description: str, max_rounds: int = 0) -> Dict:
        """Simulates a structured discussion among LLMs."""
        transcript = []
        context = task_description

        for round_num in range(max_rounds):
            round_transcript = {"round": round_num + 1, "responses": []}
            print(f"\n--- Round {round_num + 1} ---")

            for llm_idx, llm in enumerate(self.llms):
                prompt = f"Current discussion context: {context}\nWhat is your input for this round?"
                response = llm.generate_response(prompt)
                
                # Summarize the discussion in one sentence
                summary = llm.generate_response(f"Summarize in one sentence: {response}")

                context += f"\nLLM-{llm_idx + 1}: {summary}"
                round_transcript["responses"].append({"LLM": f"LLM-{llm_idx + 1}", "response": response, "summary": summary})

            transcript.append(round_transcript)

        return {"transcript": transcript, "final_output": context}

def thematic_coding(llms: List[LLMManager], comment: str) -> Dict[str, str]:
    """Assigns each LLM to generate a qualitative code for the full comment."""
    codes = {}
    for idx, llm in enumerate(llms):
        response = llm.generate_response(f"A code is often a word or short phrase that symbolically assigns a summative, salient, essence-capturing and/or evocative attribute to a portion of language-based or visual data. Perform thematic analysis on the following comment and generate a concise qualitative code:\n\n{comment}")
        codes[f"LLM-{idx + 1}"] = response
    return codes

def simulate_coding_discussion(llms: List[LLMManager], initial_codes: Dict[str, str]) -> Dict:
    """Simulates a discussion where LLMs refine qualitative codes together."""
    context = "Here are the initial codes proposed by each LLM:\n"
    memory = {}

    for llm, code in initial_codes.items():
        context += f"{llm}: {code}\n"
        memory[llm] = {"initial_code": code, "discussions": []}

    context += "\nCompare and refine the codes collaboratively."

    discussion_transcript = []
    for round_num in range(0):
        round_responses = []
        print(f"\n--- Round {round_num + 1} ---")

        for idx, llm in enumerate(llms):
            llm_id = f"LLM-{idx + 1}"
            prompt = f"Context: {context}\n\nWhat refinements do you suggest?"
            response = llm.generate_response(prompt)

            summary = llm.generate_response(f"Summarize in one sentence: {response}")
            memory[llm_id]["discussions"].append(summary)

            context += f"\n{llm_id}: {summary}"
            round_responses.append({"LLM": llm_id, "response": response, "summary": summary})

        discussion_transcript.append({"round": round_num + 1, "responses": round_responses})

    final_responses = []
    for idx, llm in enumerate(llms):
        final_context = "Final discussion summary:\n" + "\n".join(
            [summary for mem in memory.values() for summary in mem["discussions"]]
        )
        response = llm.generate_response(f"{final_context}\n\nGenerate the final agreed qualitative code.")
        final_responses.append({"LLM": f"LLM-{idx + 1}", "response": response})

    return {
        "initial_codes": initial_codes,
        "discussion_transcript": discussion_transcript,
        "final_codes": [res["response"] for res in final_responses],
        "memory": memory,
    }

def run_thematic_analysis(simulator, long_text_df: pd.DataFrame):
    """Runs the thematic analysis workflow on sampled long comments."""
    sampled_comments = long_text_df[0:500]["comment_text_x"].tolist()

    results = []
    for i, comment in enumerate(sampled_comments):
        print(f"\nProcessing comment {i+1}/{500}...\n")

        print("\nStep 1: Initial Thematic Coding")
        codes = thematic_coding(simulator.llms, comment)

        print("\nStep 2: LLMs Discuss and Refine Codes")
        discussion_results = simulate_coding_discussion(simulator.llms, codes)

        print("\nFinal Agreed Code:")
        print(discussion_results["final_codes"])

        results.append({
            "comment": comment,
            "initial_codes": codes,
            "discussion_results": discussion_results,
        })

    with open("results_0r_mixtral_llama70b_deepseek.json", "w") as f:
        json.dump(results, f, indent=2)

def main():
    """Main function to run the experiment on long comments."""
    llms = [
        LLMManager(model_name="mixtral-8x7b-32768"),
        LLMManager(model_name="llama-3.3-70b-versatile"),
        LLMManager(model_name="deepseek-r1-distill-qwen-32b"),
    ]

    simulator = DiscussionSimulator(llms)

    # Load and filter long comments
    file_path = "csv files/filtered_disagreement_identity_cases.csv"  # Ensure this file is prepared
    df = pd.read_csv(file_path)

    # Define long comment threshold (e.g., at least 100 words)
    df["word_count"] = df["comment_text_x"].apply(lambda x: len(str(x).split()))
    long_text_df = df[df["word_count"] > 100]

    if long_text_df.empty:
        print("No long comments found in dataset.")
        return

    run_thematic_analysis(simulator, long_text_df)

if __name__ == "__main__":
    main()



Processing comment 1/500...


Step 1: Initial Thematic Coding

Step 2: LLMs Discuss and Refine Codes

Final Agreed Code:
['Based on our discussion, the final agreed qualitative code is:\n\nCode: Coping Mechanisms\n\nDefinition: The ways in which individuals deal with stress, adversity, or trauma, which may include cognitive, emotional, or behavioral strategies.\n\nExamples:\n\n* Seeking social support from friends, family, or professionals\n* Engaging in leisure activities or hobbies\n* Practicing mindfulness or meditation\n* Using positive self-talk or affirmations\n* Seeking professional help, such as therapy or counseling\n* Using substances or addictive behaviors to cope\n* Engaging in avoidance or denial\n* Using humor or creativity to manage stress\n* Practicing self-care, such as exercise or healthy eating\n* Using religious or spiritual practices\n* Using problem-solving or planning strategies\n\nNote: This code can be further broken down into sub-codes based on the specific t

In [15]:
import os
import random
import json
import pandas as pd
from typing import List, Dict
from groq import Groq  

with open('api_key.txt', 'r') as file:
    api_key = file.read().strip()

client = Groq(api_key=api_key)

class LLMManager:
    """Manages interactions with Groq API-based LLMs."""

    def __init__(self, model_name: str):
        self.model_name = model_name

    def generate_response(self, prompt: str) -> str:
        """Generates response using Groq API."""
        try:
            chat_completion = client.chat.completions.create(
                messages=[{"role": "user", "content": prompt}],
                model=self.model_name,  # Example: "mixtral-8x7b-32768"
            )
            response = chat_completion.choices[0].message.content
            return response.strip()
        except Exception as e:
            print(f"Error generating response: {e}")
            return "Error generating response."

class DiscussionSimulator:
    """Simulates discussions among multiple LLMs."""

    def __init__(self, llms: List[LLMManager]):
        self.llms = llms

    def simulate_discussion(self, task_description: str, max_rounds: int = 5) -> Dict:
        """Simulates a structured discussion among LLMs."""
        transcript = []
        context = task_description

        for round_num in range(max_rounds):
            round_transcript = {"round": round_num + 1, "responses": []}
            print(f"\n--- Round {round_num + 1} ---")

            for llm_idx, llm in enumerate(self.llms):
                prompt = f"Current discussion context: {context}\nWhat is your input for this round?"
                response = llm.generate_response(prompt)
                
                # Summarize the discussion in one sentence
                summary = llm.generate_response(f"Summarize in one sentence: {response}")

                context += f"\nLLM-{llm_idx + 1}: {summary}"
                round_transcript["responses"].append({"LLM": f"LLM-{llm_idx + 1}", "response": response, "summary": summary})

            transcript.append(round_transcript)

        return {"transcript": transcript, "final_output": context}

def thematic_coding(llms: List[LLMManager], comment: str) -> Dict[str, str]:
    """Assigns each LLM to generate a qualitative code for the full comment."""
    codes = {}
    for idx, llm in enumerate(llms):
        response = llm.generate_response(f"A code is often a word or short phrase that symbolically assigns a summative, salient, essence-capturing and/or evocative attribute to a portion of language-based or visual data. Perform thematic analysis on the following comment and generate a concise qualitative code:\n\n{comment}")
        codes[f"LLM-{idx + 1}"] = response
    return codes

def simulate_coding_discussion(llms: List[LLMManager], initial_codes: Dict[str, str]) -> Dict:
    """Simulates a discussion where LLMs refine qualitative codes together."""
    context = "Here are the initial codes proposed by each LLM:\n"
    memory = {}

    for llm, code in initial_codes.items():
        context += f"{llm}: {code}\n"
        memory[llm] = {"initial_code": code, "discussions": []}

    context += "\nCompare and refine the codes collaboratively."

    discussion_transcript = []
    for round_num in range(3):
        round_responses = []
        print(f"\n--- Round {round_num + 1} ---")

        for idx, llm in enumerate(llms):
            llm_id = f"LLM-{idx + 1}"
            prompt = f"Context: {context}\n\nWhat refinements do you suggest?"
            response = llm.generate_response(prompt)

            summary = llm.generate_response(f"Summarize in one sentence: {response}")
            memory[llm_id]["discussions"].append(summary)

            context += f"\n{llm_id}: {summary}"
            round_responses.append({"LLM": llm_id, "response": response, "summary": summary})

        discussion_transcript.append({"round": round_num + 1, "responses": round_responses})

    final_responses = []
    for idx, llm in enumerate(llms):
        final_context = "Final discussion summary:\n" + "\n".join(
            [summary for mem in memory.values() for summary in mem["discussions"]]
        )
        response = llm.generate_response(f"{final_context}\n\nGenerate the final agreed qualitative code.")
        final_responses.append({"LLM": f"LLM-{idx + 1}", "response": response})

    return {
        "initial_codes": initial_codes,
        "discussion_transcript": discussion_transcript,
        "final_codes": [res["response"] for res in final_responses],
        "memory": memory,
    }

def run_thematic_analysis(simulator, long_text_df: pd.DataFrame):
    """Runs the thematic analysis workflow on sampled long comments."""
    sampled_comments = long_text_df["comment_text_x"].tolist()

    results = []
    for i, comment in enumerate(sampled_comments):
        print(f"\nProcessing comment {i+1}/{100}...\n")

        print("\nStep 1: Initial Thematic Coding")
        codes = thematic_coding(simulator.llms, comment)

        print("\nStep 2: LLMs Discuss and Refine Codes")
        discussion_results = simulate_coding_discussion(simulator.llms, codes)

        print("\nFinal Agreed Code:")
        print(discussion_results["final_codes"])

        results.append({
            "comment": comment,
            "initial_codes": codes,
            "discussion_results": discussion_results,
        })

    with open("results_3r_mixtral_llama70b.json", "w") as f:
        json.dump(results, f, indent=2)

def main():
    """Main function to run the experiment on long comments."""
    llms = [
        LLMManager(model_name="mixtral-8x7b-32768"),
        LLMManager(model_name="llama-3.3-70b-versatile")
        # LLMManager(model_name="deepseek-r1-distill-qwen-32b"),
    ]

    simulator = DiscussionSimulator(llms)

    # Load and filter long comments
    file_path = "filtered_disagreement_identity_cases.csv"  # Ensure this file is prepared
    df = pd.read_csv(file_path)

    # Define long comment threshold (e.g., at least 100 words)
    df["word_count"] = df["comment_text_x"].apply(lambda x: len(str(x).split()))
    long_text_df = df[df["word_count"] > 100]

    if long_text_df.empty:
        print("No long comments found in dataset.")
        return

    run_thematic_analysis(simulator, long_text_df)

if __name__ == "__main__":
    main()



Processing comment 1/100...


Step 1: Initial Thematic Coding

Step 2: LLMs Discuss and Refine Codes

--- Round 1 ---

--- Round 2 ---

--- Round 3 ---

Final Agreed Code:
['"Defending Mother\'s Public Health Legacy"\n\nThis code captures the essence of the comment as a defensive and proud response to criticism of the author\'s mother\'s significant contributions to public health, specifically safety laws and asthma advice, while addressing historical misconceptions about the tobacco industry and promoting moderation. It also emphasizes the emotional tone and context of the comment and concisely conveys the author\'s intent in a simple and clear manner.', 'Based on the discussion summary, the final agreed qualitative code is:\n\n"Defending Mother\'s Public Health Legacy"\n\nThis code accurately captures the essence of the comment, reflecting the author\'s defensive and proud response to criticism of their mother\'s significant contributions to public health, specifically safety laws a


Processing comment 1/100...


Step 1: Initial Thematic Coding

Step 2: LLMs Discuss and Refine Codes

--- Round 1 ---

--- Round 2 ---

--- Round 3 ---

Final Agreed Code:
["**Challenging Trump's Public Office Suitability due to Hate Speech and Divisive Rhetoric**", "Based on the discussion, the final agreed qualitative code is:\n\n**Challenging Trump's Public Office Suitability due to Hate Speech and Divisive Rhetoric**\n\nThis code effectively captures the main theme of comments critiquing Donald Trump's language and behavior, and it is a concise and clear summary that prioritizes clarity and concision."]

Processing comment 2/100...


Step 1: Initial Thematic Coding

Step 2: LLMs Discuss and Refine Codes

--- Round 1 ---

--- Round 2 ---

--- Round 3 ---

Final Agreed Code:
['"Proactively addressing and mitigating personal and systemic biases through heightened self-awareness, specific strategies, and actionable efforts to foster equity, fairness, and inclusivity, acknowledging the

In [ ]:
## Analyzing json files

In [26]:
!pip install openai==0.28

In [ ]:
#Putting to csv table

In [64]:
#3 models 5 rounds
import openai
import json
import pandas as pd

with open('openai_key.txt', 'r') as file:
    api_key = file.read().strip()

# Set your OpenAI API key
OPENAI_API_KEY = api_key
openai.api_key = api_key

def extract_code(comment, llm_name):
    prompt = f"""
    Extract only the qualitative code from this response.

    Comment: {comment}

    """
    
    try:
        response = openai.ChatCompletion.create(
            model="gpt-4o",
            messages=[{"role": "system", "content": ""},
                      {"role": "user", "content": prompt}],
            temperature=0.0
        )
        return response["choices"][0]["message"]["content"].strip().replace('"', '')  # Remove quotes if any
    except Exception as e:
        print(f"Error extracting code for {llm_name}: {e}")
        return "Error"

# Load the JSON file
with open("results_1r_mixtral_llama70b_deepseek.json", "r", encoding="utf-8") as file:
    data = json.load(file)

# Define DataFrame structure
columns = [
    "Comment", "Llama 70B", "Mixtral", "Deepseek", 
    "Llama 70B Round1", "Mixtral Round1", "Deepseek Round1",
    "Llama 70B Final", "Mixtral Final", "Deepseek Final"
]
df = pd.DataFrame(columns=columns)

# Process each discussion comment
for discussion in data:
    comment = discussion.get("comment", "")
    initial_codes = discussion.get("initial_codes", "")
    print(comment)
    discussion_results = discussion.get("discussion_results", "")
    discussion_transcript=discussion_results['discussion_transcript']
    final_codes = discussion_results['final_codes']

    # Generate only the extracted code
    llama70b_code = extract_code(initial_codes['LLM-1'], "Llama 70B")
    mixtral_code = extract_code(initial_codes['LLM-2'], "Mixtral")
    deepseek_code = extract_code(initial_codes['LLM-3'], "Deepseek")
    # qwen_code = extract_code(initial_codes['LLM-4'], "Qwen")
    # gemma_code = extract_code(initial_codes['LLM-5'], "Gemma")

    # Extract discussion round codes
    llama70b_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B Round1")
    mixtral_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral Round1")
    deepseek_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek Round1")
    #qwen_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-4"),"No matching response found" ), "Qwen Round1")
    #gemma_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-5"),"No matching response found" ), "Gemma Round1")


    #llama70b_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R2")
   # mixtral_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R2")
   # deepseek_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R2")
   # qwen_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-4"),"No matching response found" ), "Qwen R2")
    #gemma_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-5"),"No matching response found" ), "Gemma R2")

   # llama70b_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R3")
   # mixtral_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R3")
   # deepseek_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R3")
    #qwen_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-4"),"No matching response found" ), "Qwen R3")
   # gemma_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-5"),"No matching response found" ), "Gemma R3")

   # llama70b_r4 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 4 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R4")
   # mixtral_r4 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 4 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R4")
   # deepseek_r4 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 4 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R4")
    # Generate final codes
    
    #llama70b_r5 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 5 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R5")
    #mixtral_r5 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 5 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R5")
    #deepseek_r5 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 5 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R5")
    # Generate final codes
    
    llama70b_final = extract_code(final_codes[0], "Llama 70B Final")
    mixtral_final = extract_code(final_codes[1], "Mixtral Final")
    deepseek_final = extract_code(final_codes[2], "Deepseek Final")
   # qwen_final = extract_code(final_codes[3], "Qwen Final")
   # gemma_final = extract_code(final_codes[4], "Gemma Final")

    # Append the new row to the DataFrame
    new_row = {
        "Comment": comment,
        "Llama 70B": llama70b_code, "Mixtral": mixtral_code, "Deepseek": deepseek_code, 
        "Llama 70B Round1": llama70b_r1, "Mixtral Round1": mixtral_r1, "Deepseek Round1": deepseek_r1, 
        "Llama 70B Final": llama70b_final, "Mixtral Final": mixtral_final, "Deepseek Final": deepseek_final,
    }
    
    df = pd.concat([df, pd.DataFrame([new_row])], ignore_index=True)

# Save to CSV
df.to_csv("extracted_LLM_codes_3models_1rounds.csv", index=False)

print("Extraction complete! CSV saved as 'extracted_LLM_codes.csv'.")


Part 3
The owner of Remedy Wine Bar (which closes in days) asked people why they sh*t in his doorway when there is a Public Loo nearby.  Answer: Drug Dealers don’t allow them to use the loo; they’re doing business. 

Allowing that segment of the squatters who suffer (a) from mental illness or (b) addiction to rot outside is not an act of compassion.  If the Police may not engage, then they cannot triage.  YOU and Mayor Hales are, literally, killing them with your kindness. 

If you think I’m an illiberal jerk, I’ll tell that I gave a year of my life (unpaid) to the Democratic Party in an effort to make Oregon a one-party state.  

Now, it is time for Democrats to evolve.

P.S.  Would you prefer a locked gate or armed guards?
Militia's aren't your friend nor are they trying to protect or help anyone except themselves.  Please inform yourselves about what Sovereign Citizen Movement Militias are trying to do.  This militia group associated with this philosophy of Sovereign Citizens who be

In [ ]:
## Processing discussions

In [79]:
#3 models processing

import openai
import json
import pandas as pd


# Function to call GPT-4o API and extract only the code
def extract_code(comment, llm_name):
    return comment 


# Load the JSON file
with open("results_3r_mixtral_llama70b_qwen_deepseek_gemma_1.json", "r", encoding="utf-8") as file:
    data = json.load(file)

# Define DataFrame structure
columns = [
    "Comment", "Llama 70B", "Mixtral", "Deepseek", "Qwen", "Gemma",
    "Llama 70B Round1", "Mixtral Round1", "Deepseek Round1","Qwen Round1", "Gemma Round1",
    "Llama 70B R2", "Mixtral R2", "Deepseek R2","Qwen R2", "Gemma R2",
    "Llama 70B R3", "Mixtral R3", "Deepseek R3","Qwen R3", "Gemma R3",
    # "Llama 70B R4", "Mixtral R4", "Deepseek R4","Qwen R4", "Gemma R4",
    # "Llama 70B R5", "Mixtral R5", "Deepseek R5","Qwen R5", "Gemma R5",
    "Llama 70B Final", "Mixtral Final", "Deepseek Final","Qwen Final", "Gemma Final"
]
df = pd.DataFrame(columns=columns)

# Process each discussion comment
for discussion in data:
    comment = discussion.get("comment", "")
    initial_codes = discussion.get("initial_codes", "")
    print(comment)
    discussion_results = discussion.get("discussion_results", "")
    discussion_transcript=discussion_results['discussion_transcript']
    final_codes = discussion_results['final_codes']

    # Generate only the extracted code
    llama70b_code = extract_code(initial_codes['LLM-1'], "Llama 70B")
    mixtral_code = extract_code(initial_codes['LLM-2'], "Mixtral")
    deepseek_code = extract_code(initial_codes['LLM-3'], "Deepseek")
    qwen_code = extract_code(initial_codes['LLM-4'], "Qwen")
    gemma_code = extract_code(initial_codes['LLM-5'], "Gemma")

    # Extract discussion round codes
    llama70b_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B Round1")
    mixtral_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral Round1")
    deepseek_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek Round1")
    qwen_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-4"),"No matching response found" ), "Qwen Round1")
    gemma_r1 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 1 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-5"),"No matching response found" ), "Gemma Round1")

    
    llama70b_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R2")
    mixtral_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R2")
    deepseek_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R2")
    qwen_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-4"),"No matching response found" ), "Qwen R2")
    gemma_r2 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 2 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-5"),"No matching response found" ), "Gemma R2")

    
    llama70b_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R3")
    mixtral_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R3")
    deepseek_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R3")
    qwen_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-4"),"No matching response found" ), "Qwen R3")
    gemma_r3 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 3 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-5"),"No matching response found" ), "Gemma R3")


    
    # llama70b_r4 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 4 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R4")
    # mixtral_r4 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 4 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R4")
    # deepseek_r4 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 4 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R4")

    # llama70b_r5 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 5 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-1"),"No matching response found" ), "Llama 70B R5")
    # mixtral_r5 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 5 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-2"),"No matching response found" ), "Mixtral R5")
    # deepseek_r5 = extract_code(next((resp.get("response", "No response available") for round_data in discussion_transcript if round_data.get("round") == 5 for resp in round_data.get("responses", []) if resp.get("LLM") == "LLM-3"),"No matching response found" ), "Deepseek R5")

    # Generate final codes
    llama70b_final = extract_code(final_codes[0], "Llama 70B Final")
    mixtral_final = extract_code(final_codes[1], "Mixtral Final")
    deepseek_final = extract_code(final_codes[2], "Deepseek Final")
    qwen_final = extract_code(final_codes[3], "Qwen Final")
    gemma_final = extract_code(final_codes[4], "Gemma Final")

    # Append the new row to the DataFrame
    new_row = {
        "Comment": comment,
        "Llama 70B": llama70b_code, "Mixtral": mixtral_code, "Deepseek": deepseek_code, "Qwen": qwen_code, "Gemma": gemma_code,
        "Llama 70B Round1": llama70b_r1, "Mixtral Round1": mixtral_r1, "Deepseek Round1": deepseek_r1, "Qwen Round1": qwen_r1, "Gemma Round1": gemma_r1,
        "Llama 70B R2": llama70b_r2, "Mixtral R2": mixtral_r2, "Deepseek R2": deepseek_r2,"Qwen R2": qwen_r2,"Gemma R2": gemma_r2,
        "Llama 70B R3": llama70b_r3, "Mixtral R3": mixtral_r3, "Deepseek R3": deepseek_r3,"Qwen R3": qwen_r3,"Gemma R3": gemma_r3,
        # "Llama 70B R4": llama70b_r4, "Mixtral R4": mixtral_r4, "Deepseek R4": deepseek_r4,
        # "Llama 70B R5": llama70b_r5, "Mixtral R5": mixtral_r5, "Deepseek R5": deepseek_r5,
        "Llama 70B Final": llama70b_final, "Mixtral Final": mixtral_final, "Deepseek Final": deepseek_final, "Qwen Final": qwen_final,"Gemma Final": gemma_final
    }
    
    df = pd.concat([df, pd.DataFrame([new_row])], ignore_index=True)

# Save to CSV
df.to_csv("extracted_discussion_3r_5models.csv", index=False)

print("Extraction complete! CSV saved as 'extracted_LLM_codes.csv'.")


Part 3
The owner of Remedy Wine Bar (which closes in days) asked people why they sh*t in his doorway when there is a Public Loo nearby.  Answer: Drug Dealers don’t allow them to use the loo; they’re doing business. 

Allowing that segment of the squatters who suffer (a) from mental illness or (b) addiction to rot outside is not an act of compassion.  If the Police may not engage, then they cannot triage.  YOU and Mayor Hales are, literally, killing them with your kindness. 

If you think I’m an illiberal jerk, I’ll tell that I gave a year of my life (unpaid) to the Democratic Party in an effort to make Oregon a one-party state.  

Now, it is time for Democrats to evolve.

P.S.  Would you prefer a locked gate or armed guards?
Militia's aren't your friend nor are they trying to protect or help anyone except themselves.  Please inform yourselves about what Sovereign Citizen Movement Militias are trying to do.  This militia group associated with this philosophy of Sovereign Citizens who be

In [28]:
df

Comment  \
0  Part 3\nThe owner of Remedy Wine Bar (which cl...   
1  Militia's aren't your friend nor are they tryi...   
2  Well, this wasn't meant to be a dissertation. ...   

                                           Llama 70B                  Mixtral  \
0   Enabling homelessness through misguided kindness  Compassion vs. Enabling   
1  Dangerous, Lawless, Extremist Militias promoti...      Dangerous Extremism   
2  Skeptical humor with a respect for individual ...           Tolerant Humor   

                               Deepseek  \
0    **Code:** Compassion as Complicity   
1            Dangerous Extremist Groups   
2  Humor and Atheism: A Respectful Take   

                           Llama 70B Round1  \
0  Misguided Compassion as Systemic Neglect   
1        Anti-government Extremist Militias   
2           Humorous and Respectful Atheism   

                                 Mixtral Round1  \
0  Compassion as Complicity in Systemic Neglect   
1                   Sovereign Citizen Extremism   
2   Humorous Atheism with Respectful Skepticism   

                                     Deepseek Round1  \
0  The qualitative code extracted from the respon...   
1  **Qualitative Code: Violent Sovereign Citizen ...   
2               Humor and Atheism: A Respectful Take   

                                        Llama 70B R2  \
0  Compassion as Complicity in Neglect  \nMisguid...   
1                Violent Sovereign Citizen Extremism   
2     Humorous Atheism Promoting Respectful Dialogue   

                                          Mixtral R2  \
0  - Compassion as Complicity in Neglect (LLM-3)\...   
1  1. Violent Anti-Government Extremism\n2. Sover...   
2        Humorous Atheism with Respectful Skepticism   

                                         Deepseek R2  \
0                Compassion as Complicity in Neglect   
1  The user considered various codes to describe ...   
2                    Humorous and Respectful Atheism   

                                        Llama 70B R3  \
0  The qualitative code extracted from the respon...   
1                Violent Sovereign Citizen Extremism   
2  Humorous Atheism Respecting Philosophical Diff...   

                                          Mixtral R3  \
0       Compassion as Complicity in Systemic Neglect   
1  1. Violent Anti-Government Extremism\n2. Sover...   
2                    Humorous and Respectful Atheism   

                                         Deepseek R3  \
0  **Code:** Compassion as Complicity in Systemic...   
1                Violent Sovereign Citizen Extremism   
2  **Final Refinement: Humorous and Respectful At...   

                                Llama 70B Final  \
0  Compassion as Complicity in Systemic Neglect   
1                   Sovereign Citizen Extremism   
2               Humorous and Respectful Atheism   

                         Mixtral Final  \
0  Compassion as Complicity in Neglect   
1  Violent Sovereign Citizen Extremism   
2      Humorous and Respectful Atheism   

                                      Deepseek Final  
0  **Code:** Compassion as Complicity in Systemic...  
1                Violent Sovereign Citizen Extremism  
2  **Final Agreed Qualitative Code:** Humorous an...